In [ ]:
!apt install swig cmake ffmpeg xvfb python3-opengl
!pip install stable-baselines3==2.0.0a5 gymnasium[box2d] huggingface_sb3 pyvirtualdisplay imageio[ffmpeg]

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
cmake is already the newest version (3.22.1-1ubuntu1.22.04.2).
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
The following additional packages will be installed:
  freeglut3 libfontenc1 libglu1-mesa libxfont2 libxkbfile1 swig4.0 x11-xkb-utils xfonts-base
  xfonts-encodings xfonts-utils xserver-common
Suggested packages:
  libgle3 python3-numpy swig-doc swig-examples swig4.0-examples swig4.0-doc
The following NEW packages will be installed:
  freeglut3 libfontenc1 libglu1-mesa libxfont2 libxkbfile1 python3-opengl swig swig4.0
  x11-xkb-utils xfonts-base xfonts-encodings xfonts-utils xserver-common xvfb
0 upgraded, 14 newly installed, 0 to remove and 45 not upgraded.
Need to get 9,755 kB of archives.
After this operation, 25.6 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 freeglut3 amd64 2.8.1-6 [74.0 kB]
Get:2 http://

In [ ]:
import os
os.kill(os.getpid(), 9)

In [ ]:
from pyvirtualdisplay import Display
virtual_display = Display(visible=0, size=(1400, 900))
virtual_display.start()

In [ ]:
import gymnasium as gym
env = gym.make("BipedalWalker-v3", hardcore=True)
env.reset()

(array([ 2.7474952e-03, -7.6986189e-06,  5.9886085e-04, -1.5999949e-02,
         9.2043772e-02, -7.9029059e-04,  8.6022151e-01,  1.9871613e-03,
         1.0000000e+00,  3.2449905e-02, -7.9023471e-04,  8.5377008e-01,
         5.5890071e-04,  1.0000000e+00,  4.4081402e-01,  4.4582012e-01,
         4.6142277e-01,  4.8955020e-01,  5.3410280e-01,  6.0246104e-01,
         7.0914888e-01,  8.8593185e-01,  9.7504199e-01,  1.0000000e+00],
       dtype=float32),
 {})

In [ ]:
print("_____OBSERVATION SPACE_____ \n")
print("Observation Space Shape", env.observation_space.shape)
print("Sample observation", env.observation_space.sample())

_____OBSERVATION SPACE_____ 

Observation Space Shape (24,)
Sample observation [-0.4656293   2.0788429   0.99933034  1.7298229   2.1831362  -4.522843
  1.1337125   1.7218583   0.01144379 -0.78679734  4.37409    -3.057316
 -3.8493676   0.5289197   0.85657644  0.69657767  0.678749    0.8453108
  0.09627609 -0.7312284  -0.46962577  0.79437554  0.9155286  -0.73020685]


In [ ]:
print("\n _____ACTION SPACE_____ \n")
print("Action Space Shape", env.action_space.shape)
print("Action Space Sample", env.action_space.sample())


 _____ACTION SPACE_____ 

Action Space Shape (4,)
Action Space Sample [ 0.245747    0.1738644   0.16663465 -0.52753764]


In [ ]:
from stable_baselines3.common.env_util import make_vec_env
env = make_vec_env('BipedalWalker-v3', n_envs=1)

In [ ]:
from stable_baselines3 import TD3  # Import TD3 algorithm

# Use TD3 algorithm
model = TD3(
    policy='MlpPolicy',
    env=env,
    verbose=1
)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Using cpu device


In [ ]:
from wasabi import Printer
import numpy as np
from stable_baselines3.common.base_class import BaseAlgorithm
from pathlib import Path
import tempfile
from stable_baselines3.common.monitor import Monitor
from stable_baselines3.common.vec_env import (
    DummyVecEnv,
    VecEnv,
    VecVideoRecorder,
)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [ ]:
msg = Printer()

In [ ]:
def generate_replay(
    model: BaseAlgorithm,
    eval_env: VecEnv,
    video_length: int,
    is_deterministic: bool,
    local_path: Path,
):
    """
    Generate a replay video of the agent
    :param model: trained model
    :param eval_env: environment used to evaluate the agent
    :param video_length: length of the video (in timesteps)
    :param is_deterministic: use deterministic or stochastic actions
    :param local_path: path of the local repository
    """
    # This is another temporary directory for video outputs
    # SB3 created a -step-0-to-... meta files as well as other
    # artifacts which we don't want in the repo.
    with tempfile.TemporaryDirectory() as tmpdirname:
        # Step 1: Create the VecVideoRecorder
        env = VecVideoRecorder(
            eval_env,
            tmpdirname,
            record_video_trigger=lambda x: x == 0,
            video_length=video_length,
            name_prefix="",
        )

        obs = env.reset()
        lstm_states = None
        episode_starts = np.ones((env.num_envs,), dtype=bool)

        try:
            for _ in range(video_length):
                action, lstm_states = model.predict(
                    obs,
                    state=lstm_states,
                    episode_start=episode_starts,
                    deterministic=is_deterministic,
                )
                obs, _, episode_starts, _ = env.step(action)

            # Save the video
            env.close()

            # Convert the video with x264 codec
            inp = env.video_recorder.path
            out = local_path
            os.system(f"ffmpeg -y -i {inp} -vcodec h264 {out}".format(inp, out))
            print(f"Video saved to: {out}")
        except KeyboardInterrupt:
            pass
        except Exception as e:
            msg.fail(str(e))
            # Add a message for video
            msg.fail(
                "We are unable to generate a replay of your agent"
            )

In [ ]:
import os
#create a directory to save the videos
video_dir = "/content/videos"
if not os.path.exists(video_dir):
    os.makedirs(video_dir)

In [12]:
env_id = "BipedalWalker-v3"
# Train and generate video at every 100000 steps, adjust the timesteps to your liking
for i in range(0, 200000, 10000):
    model.learn(total_timesteps=10000)
    # Save the model
    model_name = "TD3-BipedalWalker-v3"
    model.save(model_name)
    video_name = f"replay_{i + 10000}.mp4"
    generate_replay(
        model=model,
        eval_env=DummyVecEnv([lambda: Monitor(gym.make(env_id, hardcore=True, render_mode="rgb_array"))]),
        video_length=1000,
        is_deterministic=True,
        local_path=os.path.join(video_dir, video_name)
    )

model_name = "TD3-BipedalWalker-v3"
model.save(model_name)


---------------------------------
| rollout/           |          |
|    ep_len_mean     | 440      |
|    ep_rew_mean     | -129     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 551      |
|    time_elapsed    | 3        |
|    total_timesteps | 1758     |
| train/             |          |
|    actor_loss      | 1.12     |
|    critic_loss     | 203      |
|    learning_rate   | 0.001    |
|    n_updates       | 101      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 437      |
|    ep_rew_mean     | -135     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 56       |
|    time_elapsed    | 62       |
|    total_timesteps | 3493     |
| train/             |          |
|    actor_loss      | 0.801    |
|    critic_loss     | 14.2     |
|    learning_rate   | 0.001    |
|    n_updates       | 3391     |
--------------

Moviepy - Done !
Moviepy - video ready /tmp/tmpbrm3vdbg/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_10000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 98.5     |
|    ep_rew_mean     | -109     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 52       |
|    time_elapsed    | 7        |
|    total_timesteps | 394      |
| train/             |          |
|    actor_loss      | 2.42     |
|    critic_loss     | 3.46     |
|    learning_rate   | 0.001    |
|    n_updates       | 10425    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 102      |
|    ep_rew_mean     | -117     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 47       |
|    time_elapsed    | 17       |
|    total_timesteps | 814      |
| train/             |          |
|    actor_loss     

Moviepy - Done !
Moviepy - video ready /tmp/tmpwblifva6/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_20000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 450      |
|    ep_rew_mean     | -124     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 47       |
|    time_elapsed    | 37       |
|    total_timesteps | 1799     |
| train/             |          |
|    actor_loss      | 12.1     |
|    critic_loss     | 4.61     |
|    learning_rate   | 0.001    |
|    n_updates       | 23164    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 262      |
|    ep_rew_mean     | -122     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 47       |
|    time_elapsed    | 43       |
|    total_timesteps | 2098     |
| train/             |          |
|    actor_loss     

Moviepy - Done !
Moviepy - video ready /tmp/tmpx8qa0fxk/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_30000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 483      |
|    ep_rew_mean     | -112     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 262      |
|    time_elapsed    | 7        |
|    total_timesteps | 1932     |
| train/             |          |
|    actor_loss      | 19.6     |
|    critic_loss     | 8.67     |
|    learning_rate   | 0.001    |
|    n_updates       | 31851    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 688      |
|    ep_rew_mean     | -122     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 62       |
|    time_elapsed    | 88       |
|    total_timesteps | 5501     |
| train/             |          |
|    actor_loss     

Moviepy - Done !
Moviepy - video ready /tmp/tmp_txp2g5r/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_40000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 833      |
|    ep_rew_mean     | -107     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 87       |
|    time_elapsed    | 38       |
|    total_timesteps | 3332     |
| train/             |          |
|    actor_loss      | 17.1     |
|    critic_loss     | 6.47     |
|    learning_rate   | 0.001    |
|    n_updates       | 43660    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 640      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 8        |
|    fps             | 47       |
|    time_elapsed    | 108      |
|    total_timesteps | 5123     |
| train/             |          |
|    actor_loss     

...

Moviepy - Done !
Moviepy - video ready /tmp/tmpfo4tv_xz/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_160000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.6e+03  |
|    ep_rew_mean     | -85.8    |
| time/              |          |
|    episodes        | 4        |
|    fps             | 37       |
|    time_elapsed    | 170      |
|    total_timesteps | 6400     |
| train/             |          |
|    actor_loss      | 12.9     |
|    critic_loss     | 1.58     |
|    learning_rate   | 0.001    |
|    n_updates       | 178696   |
---------------------------------
Saving video to /tmp/tmp177zs3b1/-step-0-to-step-1000.mp4
Moviepy - Building video /tmp/tmp177zs3b1/-step-0-to-step-1000.mp4.
Moviepy - Writing video /tmp/tmp177zs3b1/-step-0-to-step-1000.mp4



Moviepy - Done !
Moviepy - video ready /tmp/tmp177zs3b1/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_170000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.22e+03 |
|    ep_rew_mean     | -82.2    |
| time/              |          |
|    episodes        | 4        |
|    fps             | 42       |
|    time_elapsed    | 113      |
|    total_timesteps | 4881     |
| train/             |          |
|    actor_loss      | 12.9     |
|    critic_loss     | 1.43     |
|    learning_rate   | 0.001    |
|    n_updates       | 187412   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.41e+03 |
|    ep_rew_mean     | -85.5    |
| time/              |          |
|    episodes        | 8        |
|    fps             | 32       |
|    time_elapsed    | 344      |
|    total_timesteps | 11281    |
| train/             |          |
|    actor_loss    

Moviepy - Done !
Moviepy - video ready /tmp/tmpeod37rob/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_180000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.21e+03 |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 42       |
|    time_elapsed    | 113      |
|    total_timesteps | 4853     |
| train/             |          |
|    actor_loss      | 12.9     |
|    critic_loss     | 1.12     |
|    learning_rate   | 0.001    |
|    n_updates       | 198612   |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.41e+03 |
|    ep_rew_mean     | -87.7    |
| time/              |          |
|    episodes        | 8        |
|    fps             | 33       |
|    time_elapsed    | 337      |
|    total_timesteps | 11253    |
| train/             |          |
|    actor_loss    

Moviepy - Done !
Moviepy - video ready /tmp/tmpyksqwj3l/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_190000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.6e+03  |
|    ep_rew_mean     | -93      |
| time/              |          |
|    episodes        | 4        |
|    fps             | 37       |
|    time_elapsed    | 170      |
|    total_timesteps | 6400     |
| train/             |          |
|    actor_loss      | 11.8     |
|    critic_loss     | 1.08     |
|    learning_rate   | 0.001    |
|    n_updates       | 211412   |
---------------------------------
Saving video to /tmp/tmpi1fh534k/-step-0-to-step-1000.mp4
Moviepy - Building video /tmp/tmpi1fh534k/-step-0-to-step-1000.mp4.
Moviepy - Writing video /tmp/tmpi1fh534k/-step-0-to-step-1000.mp4



Moviepy - Done !
Moviepy - video ready /tmp/tmpi1fh534k/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_200000.mp4


In [13]:
with open(os.path.join(video_dir, "filelist.txt"), "w") as f:
    for i in range(0, 200000, 10000):
        video_name = f"replay_{i + 10000}.mp4"
        f.write(f"file '{os.path.join(video_dir, video_name)}'\n")
# Concatenate all the videos into one
os.system(f"ffmpeg -f concat -safe 0 -i {os.path.join(video_dir, 'filelist.txt')} -c copy {os.path.join(video_dir, 'replay_all.mp4')}")

0

In [14]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open('videos/replay_all.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=600 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [15]:
from stable_baselines3.common.evaluation import evaluate_policy
eval_env = Monitor(gym.make("BipedalWalker-v3"))
mean_reward, std_reward = evaluate_policy(model, eval_env, n_eval_episodes=10, deterministic=True)
print(f"mean_reward={mean_reward:.2f} +/- {std_reward}")

mean_reward=-85.93 +/- 19.165817558701292
